In [12]:
import pandas as pd
import json
import gzip
import numpy as np
import scipy
from scipy.sparse import csr_matrix
from scipy.sparse import csc_matrix
from scipy.sparse.linalg import svds
import sklearn
from sklearn.neighbors import NearestNeighbors
from sklearn.preprocessing import normalize
import csv
from sparsesvd import sparsesvd
import math
import operator

In [13]:
def unzip_json(filename):
    
    print('Unzipping json file...')
    
    unzipped_data = pd.read_json(gzip.open(filename))
    
    return unzipped_data

In [14]:
# Output json training data as a Pandas dataframe.
def json_to_df(file_name):

    print('Converting json file to dataframe...')

    try:
        training_data = pd.read_json(file_name, lines=True)
        return training_data
    except:
        print('Please try another file name.')

        return None

In [15]:
training_df = json_to_df('reviews.training.json')

Converting json file to dataframe...


In [16]:
def convert_to_csv(dataframe, desired_filename):

    print('Converting dataframe to csv: ' + desired_filename + '...')

    try:
        return dataframe.to_csv(desired_filename, index=False)
    except:
        print('Please try another dataframe or file name.')

    return None

In [17]:
# I kept running into a bottleneck while trying to normalize the data.
# This file contains about 2/3 the amount of users as the original file while I continue optimizing.
convert_to_csv(training_df[['reviewerID', 'asin', 'overall']].head(5000), 'reviews.training.shortened.csv')

Converting dataframe to csv: reviews.training.shortened.csv...


In [18]:
# Returns dictionaries with unique users and products as keys and unique ints as values.
def create_user_product_dicts(filename):

    print('Creating dictionaries from CSV for unique users and products...')

    user_dict = {}
    product_dict = {}
    user_count = 0
    product_count = 0

    with open(filename, 'r') as train_file:
        file_reader=csv.reader(train_file, delimiter=',')
        next(file_reader, None)

        for row in file_reader:
            if row[0] not in user_dict:
                user_dict[row[0]] = user_count
                user_count += 1
            if row[1] not in product_dict:
                product_dict[row[1]] = product_count
                product_count += 1

    return user_dict, product_dict, user_count, product_count

In [19]:
user_dict, product_dict, user_count, product_count = create_user_product_dicts('reviews.training.shortened.csv')

Creating dictionaries from CSV for unique users and products...


In [20]:
def training_mtx(filename, user_dict, product_dict):

        print('Creating a dense matrix from training data...')

        num_user_ids = len(user_dict)
        num_product_ids = len(product_dict)

        dense_matrix = np.zeros(shape=(num_user_ids, num_product_ids), dtype=np.float32)

        with open(filename, 'r') as train_file:
            matrix_reader = csv.reader(train_file, delimiter=',')
            next(matrix_reader, None)
            for row in matrix_reader:
                dense_matrix[user_dict[row[0]], product_dict[row[1]]] = float(row[2])

        return dense_matrix

In [21]:
training_matrix = training_mtx('reviews.training.shortened.csv', user_dict, product_dict)

Creating a dense matrix from training data...


In [22]:
training_matrix

array([[4., 0., 0., ..., 0., 0., 0.],
       [0., 5., 0., ..., 0., 0., 0.],
       [0., 0., 5., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 4., 0., 0.],
       [0., 0., 0., ..., 0., 4., 0.],
       [0., 0., 0., ..., 0., 0., 2.]], dtype=float32)

In [23]:
training_matrix.shape

(4426, 4053)

In [26]:
# Outputs dictionaries with unique test users and test products.
def get_test_users_products(filename, training_user_dict, training_product_dict):

    print('Importing test users and products...')

    test_user_count = len(training_user_dict)
    test_product_count = len(training_product_dict)
    test_user_dict = training_user_dict.copy()
    test_product_dict = training_product_dict.copy()

    with open(filename, 'r') as test_file:
        test_reader = csv.reader(test_file, delimiter=',')
        next(test_reader, None)

        for row in test_reader:
            # Add unique users to test_user dictionary.
            if row[1] not in test_user_dict:
                test_user_dict[row[1]] = test_user_count
                test_user_count += 1
            # Add unique products to test_product dictionary.
            # print(row[2])
            if row[2] not in test_product_dict:
                test_product_dict[row[2]] = test_product_count
                test_product_count += 1

    return test_user_dict, test_product_dict

In [27]:
test_user_dict, test_product_dict = get_test_users_products('reviews.test.unlabeled.csv', user_dict, product_dict)

Importing test users and products...


In [29]:
def merged_mtx_products(filename, user_dict, test_product_dict):
    
        print('Creating a matrix with new products on the x axis...')

        num_user_ids = len(user_dict)
        num_product_ids = len(test_product_dict)

        dense_matrix = np.zeros(shape=(num_user_ids, num_product_ids), dtype=np.float32)

        with open(filename, 'r') as train_file:
            matrix_reader = csv.reader(train_file, delimiter=',')
            next(matrix_reader, None)
            for row in matrix_reader:
                dense_matrix[user_dict[row[0]], product_dict[row[1]]] = float(row[2])

        return dense_matrix

In [30]:
merged_matrix_product_rows = merged_mtx_products('reviews.training.shortened.csv', user_dict, test_product_dict)

Creating a matrix with new products on the x axis...


In [31]:
merged_matrix_product_rows.shape

(4426, 37231)

In [32]:
merged_matrix_product_rows

array([[4., 0., 0., ..., 0., 0., 0.],
       [0., 5., 0., ..., 0., 0., 0.],
       [0., 0., 5., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)

In [33]:
sum(merged_matrix_product_rows[-1,:])

2.0

In [34]:
def merged_mtx_users(filename, product_dict, test_user_dict):

        print('Creating a matrix with new users on the x axis...')

        num_product_ids = len(product_dict)
        num_user_ids = len(test_user_dict)

        dense_matrix = np.zeros(shape=(num_product_ids, num_user_ids), dtype=np.float32)

        with open(filename, 'r') as train_file:
            matrix_reader = csv.reader(train_file, delimiter=',')
            next(matrix_reader, None)
            for row in matrix_reader:
                dense_matrix[product_dict[row[1]], user_dict[row[0]]] = float(row[2])

        return dense_matrix

In [35]:
merged_matrix_user_rows = merged_mtx_users('reviews.training.shortened.csv', product_dict, test_user_dict)

Creating a matrix with new users on the x axis...


In [36]:
merged_matrix_user_rows.shape

(4053, 74271)

In [37]:
merged_matrix_user_rows

array([[4., 0., 0., ..., 0., 0., 0.],
       [0., 5., 0., ..., 0., 0., 0.],
       [0., 0., 5., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)

In [38]:
sum(merged_matrix_user_rows[-1, :])

2.0

In [39]:
def to_sparse(filename_prefix, matrix):
    print('Creating a sparse matrix...')
    try:
        # Try loading previously saved sparse matrix from file (becaues I keep crashing my kernel)
        loader = np.load(filename_prefix + '.npz')
        sparse_matrix = csr_matrix((loader['data'], loader['indices'], loader['indptr']), shape=loader['shape'], dtype=np.float32)
        loader.close()
    except:
        # Create sparse matrix from dense matrix, write to file as backup
        sparse_matrix = scipy.sparse.csr_matrix(matrix, dtype=np.float32)
        scipy.sparse.save_npz((filename_prefix + 'npz'), sparse_matrix)
    return sparse_matrix

In [40]:
sparse_merged_matrix_pr = to_sparse('sparse.merged.matrix.pr', merged_matrix_product_rows)

Creating a sparse matrix...


In [41]:
sparse_merged_matrix_pr.dtype

dtype('float32')

In [42]:
sparse_merged_matrix_pr.shape

(4426, 37231)

In [43]:
sparse_merged_matrix_ur = to_sparse('sparse.merged.matrix.ur', merged_matrix_user_rows)

Creating a sparse matrix...


In [44]:
sparse_merged_matrix_ur.shape

(4053, 74271)

In [45]:
def normalize_merged_matrix(sparse_matrix, dense_merged_matrix):

    print('Calculating global mean...')
    global_mean = sparse_matrix.sum()/(sparse_matrix != 0).sum()
    print(global_mean)
    
    print('Calculating row mean...')
    matrix_row_mean = sparse_matrix.sum(1)/(sparse_matrix != 0).sum(1)
    print(matrix_row_mean)

    print('Normalizing the data...')
    normalized_matrix = sparse_matrix.copy()
    normalized_matrix -= matrix_row_mean.reshape(-1, 1)
    
    print('Normalized matrix: ')
    print(normalized_matrix.shape)
    print(normalized_matrix)

    return normalized_matrix, matrix_row_mean, global_mean

In [46]:

normalized_matrix_products, matrix_row_mean_products, global_mean = normalize_merged_matrix(sparse_merged_matrix_pr,
                                                                                            merged_matrix_product_rows)


Calculating global mean...
4.1266
Calculating row mean...
[[4.]
 [5.]
 [5.]
 ...
 [4.]
 [4.]
 [2.]]
Normalizing the data...
Normalized matrix: 
(4426, 37231)
[[ 0. -4. -4. ... -4. -4. -4.]
 [-5.  0. -5. ... -5. -5. -5.]
 [-5. -5.  0. ... -5. -5. -5.]
 ...
 [-4. -4. -4. ... -4. -4. -4.]
 [-4. -4. -4. ... -4. -4. -4.]
 [-2. -2. -2. ... -2. -2. -2.]]


In [47]:

normalized_matrix_users, matrix_row_mean_users, global_mean = normalize_merged_matrix(sparse_merged_matrix_ur,
                                                                                     merged_matrix_user_rows)


Calculating global mean...
4.1266
Calculating row mean...
[[3.83333333]
 [5.        ]
 [5.        ]
 ...
 [4.        ]
 [4.        ]
 [2.        ]]
Normalizing the data...
Normalized matrix: 
(4053, 74271)
[[ 0.16666667 -3.83333333 -3.83333333 ... -3.83333333 -3.83333333
  -3.83333333]
 [-5.          0.         -5.         ... -5.         -5.
  -5.        ]
 [-5.         -5.          0.         ... -5.         -5.
  -5.        ]
 ...
 [-4.         -4.         -4.         ... -4.         -4.
  -4.        ]
 [-4.         -4.         -4.         ... -4.         -4.
  -4.        ]
 [-2.         -2.         -2.         ... -2.         -2.
  -2.        ]]


In [48]:
def compute_svd_from_normalized(normalized_matrix):

    print('Computing svd from de-meaned matrix...')

    U, sigma, Vt = svds(normalized_matrix, k = 100)
    S = np.diag(sigma)

    return U, S, Vt

In [49]:
U_products, S_products, Vt_products = compute_svd_from_normalized(merged_matrix_product_rows)

Computing svd from de-meaned matrix...


In [50]:
predictions_product_rows = np.dot(np.dot(U_products, S_products), Vt_products)-normalized_matrix_products

In [51]:
predictions_product_rows

matrix([[3.82811594e+00, 4.00000006e+00, 4.00000001e+00, ...,
         4.00000000e+00, 4.00000000e+00, 4.00000000e+00],
        [5.00000013e+00, 8.38604631e-14, 5.00000000e+00, ...,
         5.00000000e+00, 5.00000000e+00, 5.00000000e+00],
        [5.00000003e+00, 5.00000000e+00, 3.87654200e-15, ...,
         5.00000000e+00, 5.00000000e+00, 5.00000000e+00],
        ...,
        [4.00000001e+00, 4.00000000e+00, 4.00000000e+00, ...,
         4.00000000e+00, 4.00000000e+00, 4.00000000e+00],
        [4.00000001e+00, 4.00000000e+00, 4.00000000e+00, ...,
         4.00000000e+00, 4.00000000e+00, 4.00000000e+00],
        [2.00000000e+00, 2.00000000e+00, 2.00000000e+00, ...,
         2.00000000e+00, 2.00000000e+00, 2.00000000e+00]])

In [52]:
predictions_product_rows.shape

(4426, 37231)

In [53]:
U_users, S_users, Vt_users = compute_svd_from_normalized(merged_matrix_user_rows)

Computing svd from de-meaned matrix...


In [54]:
predictions_user_rows = np.dot(np.dot(U_users, S_users), Vt_users)-normalized_matrix_users

In [55]:
predictions_user_rows

matrix([[3.66145213e+00, 3.83333339e+00, 3.83333334e+00, ...,
         3.83333333e+00, 3.83333333e+00, 3.83333333e+00],
        [5.00000004e+00, 1.63788864e-13, 5.00000000e+00, ...,
         5.00000000e+00, 5.00000000e+00, 5.00000000e+00],
        [5.00000000e+00, 5.00000000e+00, 1.50901884e-15, ...,
         5.00000000e+00, 5.00000000e+00, 5.00000000e+00],
        ...,
        [4.00000000e+00, 4.00000000e+00, 4.00000000e+00, ...,
         4.00000000e+00, 4.00000000e+00, 4.00000000e+00],
        [4.00000000e+00, 4.00000000e+00, 4.00000000e+00, ...,
         4.00000000e+00, 4.00000000e+00, 4.00000000e+00],
        [2.00000000e+00, 2.00000000e+00, 2.00000000e+00, ...,
         2.00000000e+00, 2.00000000e+00, 2.00000000e+00]])

In [56]:
merged_prediction_matrix = np.zeros(shape=(len(test_user_dict), len(test_product_dict)))

In [57]:
merged_prediction_matrix.shape

(74271, 37231)

In [ ]:
for idx, key in enumerate(test_user_dict):
    print(key)

In [69]:
prediction = predictions_user_rows[0]

In [71]:
prediction[0, 0]

3.661452134450277

In [ ]:
def query_normalized_matrix_development(test_file, prediction_file, test_user_dict, test_product_dict,
                                predictions_product_rows, predictions_user_rows, global_mean):

    print('Reconstructing matrix and making predictions...')

    with open(test_file, 'r') as test_file:
        test_reader = csv.reader(test_file, delimiter=',')
        next(test_reader, None)
        with open(prediction_file, 'w') as outfile:
            outfile_reader = csv.writer(outfile, delimiter=',')
            outfile_reader.writerow(['datapointID', 'overall'])

            for row in test_reader:

                try: 
                # Query by product.
                    product_query = predictions_user_rows[test_product_dict[row[2]]]
                    prediction = product_query[0, test_user_dict[row[1]]]
                    outfile_reader.writerow([row[0], prediction])
                    print('Query by PRODUCT')
                    print(prediction)
                except:
                    try:
                        # Query by user (new products on x axis).
                        product_query = predictions_product_rows[test_user_dict[row[1]]]
                        prediction = product_query[0, test_product_dict[row[2]]]
                        outfile_reader.writerow([row[0], prediction])
                        print('Query by USER')
                        print(prediction)
                    except:
                        # If no matching users or products are found, make prediction based on global mean.
                        prediction = global_mean
                        outfile_reader.writerow([row[0], prediction])
                        print('No matching query: GLOBAL MEAN')
                        print(prediction)

    print('Done.')
    return None

In [ ]:
predicted_ratings = query_normalized_matrix_development('reviews.test.unlabeled.csv', 'reviews.test.labeled.csv',
                                                test_user_dict, test_product_dict, predictions_product_rows,
                                                predictions_user_rows, global_mean)

In [79]:
def query_normalized_matrix_test(test_file, prediction_file, test_user_dict, test_product_dict,
                                predictions_product_rows, predictions_user_rows, global_mean):

    print('Reconstructing matrix and making predictions...')

    with open(test_file, 'r') as test_file:
        test_reader = csv.reader(test_file, delimiter=',')
        next(test_reader, None)
        with open(prediction_file, 'w') as outfile:
            outfile_reader = csv.writer(outfile, delimiter=',')
            outfile_reader.writerow(['datapointID', 'overall'])

            for row in test_reader:

                try: 
                # Query by product.
                    product_query = predictions_user_rows[test_product_dict[row[2]]]
                    prediction = product_query[0, test_user_dict[row[1]]]
                    outfile_reader.writerow([row[0], prediction])
                    print('Query by PRODUCT')
                    print(prediction)
                except:
                    try:
                        # Query by user (new products on x axis).
                        product_query = predictions_product_rows[test_user_dict[row[1]]]
                        prediction = product_query[0, test_product_dict[row[2]]]
                        outfile_reader.writerow([row[0], prediction])
                        print('Query by USER')
                        print(prediction)
                    except:
                        # If no matching users or products are found, make prediction based on global mean.
                        prediction = global_mean
                        outfile_reader.writerow([row[0], prediction])
                        print('No matching query: GLOBAL MEAN')
                        print(prediction)

    print('Done.')
    return None

In [80]:
predicted_ratings = query_normalized_matrix_test('reviews.test.unlabeled.csv', 'reviews.test.labeled.csv',
                                                test_user_dict, test_product_dict, predictions_product_rows,
                                                predictions_user_rows, global_mean)

Reconstructing matrix and making predictions...
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
4.0
Query by PRODUCT
3.0
Query by PRODUCT
5.0
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
3.6666666666666665
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
2.5
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
5.0
Query by USER
5.0
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
4.0
No matching query: GLOBAL MEAN
4.1266
Query by USER
3.5
Query by PRODUCT
3.25
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
5.0
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by USER
5.0
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
4.25
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL

4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
5.0
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
5.0
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by USER
5.0
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by USER
5.0
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Que

Query by USER
4.4
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
1.0
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
1.0
Query by USER
5.0
No matching query: GLOBAL MEAN
4.1266
Query by USER
3.0
No matching query: GLOBAL MEAN
4.1266
Query by USER
5.0
Query by USER
5.0
Query by PRODUCT
3.0
Query by USER
1.0
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by USER
4.0
Query by PRODUCT
4.999999966023548
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
5.0
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
5.0
Query by PRODUCT
4.0
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
4.0
Query by

Query by USER
3.0
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
5.0
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
5.0
No matching query: GLOBAL MEAN
4.1266
Query by USER
3.4
Query by PRODUCT
5.0
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by USER
5.0
Query by PRODUCT
5.0
No matching query: GLOBAL MEAN
4.1266
Query by USER
4.666666666666667
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by USER
1.0
No matching query: GLOBAL MEAN
4.1266
Query by USER
3.5
Query by PRODUCT
4.0
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by PROD

No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by USER
4.0
No matching query: GLOBAL MEAN
4.1266
Query by USER
4.333333333333333
Query by PRODUCT
5.0
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
5.0
Query by PRODUCT
5.0
Query by PRODUCT
4.499999999999996
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
4.5
Query by PRODUCT
5.0
Query by PRODUCT
3.0
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
5.000000170694051
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
5.0
Query by PRODUCT
5.0
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
4.0
Query by PRODUCT
4.0
Query by USER
4.0
No mat

...

No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
4.0
No matching query: GLOBAL MEAN
4.1266
Query by USER
5.0
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
5.0
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by USER
5.0
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by USER
4.0
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
4.0
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
1.0
Query by PRODUCT
5.0
Query by PRODUCT
5.0
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
5.0
Query by USER
5.0
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
4.0
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
5.0
No matching query

5.0
Query by USER
5.0
Query by USER
2.25
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
5.0
No matching query: GLOBAL MEAN
4.1266
Query by USER
5.0
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
2.0
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
4.5
Query by PRODUCT
4.0
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by USER
4.6
Query by USER
4.5
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
3.75
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
4.0
Query by PRODUCT
5.0
Query by PRODUCT
3.0
No matching query: GLOBAL MEAN
4.1266
Query by USER
3.6666666666666665
No matching query: 

No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by USER
5.0
Query by USER
3.0
Query by PRODUCT
4.0
No matching query: GLOBAL MEAN
4.1266
Query by USER
5.0
No matching query: GLOBAL MEAN
4.1266
Query by USER
3.2
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
5.0
Query by USER
5.0
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
5.000000000000192
Query by USER
5.0
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
3.8333333333333335
Query by USER
4.0
No matching query: GLOBAL MEAN
4.1266
Query by USER
5.0
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by USER
3.875
Query by PRODUCT
5.0
Query by PRODUCT
4.5
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
3.0
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by USER
5.0
Query by PRODUCT
4.0
No matching q

4.1266
Query by PRODUCT
5.0
No matching query: GLOBAL MEAN
4.1266
Query by USER
3.5
Query by USER
4.444444444444445
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
5.0
Query by USER
3.0
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
5.0
Query by PRODUCT
1.0
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
4.333333333333333
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
4.5
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
4.75
Query by PRODUCT
4.0
Query by PRODUCT
2.5
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by USER
5.0
Query by USER
3.25
Query by USER
1.0
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
4.083333333333333
Query by USER
4.666666666666667
Query by PRODUCT
3.0
Query by PRODUCT
1.0
No matching query: GLOBAL

3.5
Query by PRODUCT
4.5
Query by PRODUCT
5.0
Query by PRODUCT
2.0
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
5.0
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by PRODUCT
4.5
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
Query by USER
5.0
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266
No matching query: GLOBAL MEAN
4.1266